In [2]:
%load_ext autoreload
%autoreload 2
%matplotlib inline
from IPython.display import Math, HTML, display, Markdown, Latex

import numpy as np
import pandas as pd
from sklearn import datasets

import seaborn as sns; sns.set()
import plotly.express as px
import plotly.graph_objects as go
import matplotlib.pyplot as plt
 
from utils.utility_plots import create_dynamic_h_plot

# Linear Regression - part 1
(Univariate Linear Regression)

Linear regression is a supervised learning method whereby we would like to fit a line in such a way that the error is minimal.  
E.g. in this notebook we try to fit a line which predict the housing prices given the average number of rooms per dwelling.

But first of all, what does a Univariate Linear Regression look like
$$h_{0}(x) = \theta_{0} + \theta_{1}x\\
or  \\
y = \alpha + \beta x  \\
or  \\
y = mx + c    \\
or  \\
y = mx + b
$$

$\theta_{1}, \beta, m$ are called the slope or gradient, how much does go the line up (or down) when we take 1 step on the X-axis  
$\theta_{0}, \alpha, c, b$ are the interceptions with the Y-axis  
  
Also notice that you can find $y = mx + b$ back inside a perceptron without an activation function $y = w_{0} + \sum_{i=1}^{n} x_{i} . w_{i}$


In [4]:
from utils.utility_plots import create_dynamic_h_plot, Data2Plot

data2plot = Data2Plot()

# create 3 dynamic figures
data2plot.prepare_dynamic_data(name='b = 0')
data2plot.prepare_dynamic_data(name='b = -0.5', panel=2)
data2plot.prepare_dynamic_data(name='b = 0.5', panel=3)

# Create a range of m (slope values)
for m in [0, 0.25, 0.5, 1, 1.5, 2, 3, 5]:
    b = 0
    data2plot.feed_dynamic_data(name='b = 0', x= np.arange(-3,3,0.25), y= [ m*x + b for x in np.arange(-3,3,0.25)])
    
    b = -0.5
    data2plot.feed_dynamic_data(name='b = -0.5',  x= np.arange(-3,3,0.25), y= [ m*x + b for x in np.arange(-3,3,0.25)])
    
    b = 0.5
    data2plot.feed_dynamic_data(name='b = 0.5',  x= np.arange(-3,3,0.25), y= [ m*x + b for x in np.arange(-3,3,0.25)])
    
    data2plot.add_frame_label(f'{m}*x + b')
    
# plot
create_dynamic_h_plot(data2plot, 
                      title="Effect of m and b",
                      x_axis_1='m*x + 0', x_range_1=[-2,2], y_range_1=[-2,2],
                      x_axis_2='m*x - 0.5', x_range_2=[-2,2], y_range_2=[-2,2],
                      x_axis_3='m*x + 0.5', x_range_3=[-2,2], y_range_3=[-2,2])

# Load the Iris dataset
*Why*, the Iris dataset? Actually it doesn't matter which data set we take but i've chosen for this dataset because it has a very simple 

In [38]:
feature_matrix, target, class_names, descr, feature_names, _ = datasets.load_iris().values()
display(Markdown('## Info'))
print(descr)

display(Markdown('## Feature Matrix'))
feature_matrix = pd.DataFrame(feature_matrix, columns=feature_names)
display(feature_matrix.head())

display(Markdown('## target'))
target = pd.DataFrame(target, columns=['y'])
display(target.head())

## Info

.. _iris_dataset:

Iris plants dataset
--------------------

**Data Set Characteristics:**

    :Number of Instances: 150 (50 in each of three classes)
    :Number of Attributes: 4 numeric, predictive attributes and the class
    :Attribute Information:
        - sepal length in cm
        - sepal width in cm
        - petal length in cm
        - petal width in cm
        - class:
                - Iris-Setosa
                - Iris-Versicolour
                - Iris-Virginica
                
    :Summary Statistics:

    ============== ==== ==== ======= ===== ====================
                    Min  Max   Mean    SD   Class Correlation
    ============== ==== ==== ======= ===== ====================
    sepal length:   4.3  7.9   5.84   0.83    0.7826
    sepal width:    2.0  4.4   3.05   0.43   -0.4194
    petal length:   1.0  6.9   3.76   1.76    0.9490  (high!)
    petal width:    0.1  2.5   1.20   0.76    0.9565  (high!)
    ============== ==== ==== ======= ===== ===========

## Feature Matrix

sepal length (cm)  sepal width (cm)  petal length (cm)  petal width (cm)
0                5.1               3.5                1.4               0.2
1                4.9               3.0                1.4               0.2
2                4.7               3.2                1.3               0.2
3                4.6               3.1                1.5               0.2
4                5.0               3.6                1.4               0.2

## target

y
0  0
1  0
2  0
3  0
4  0

# Prospect the data
If we've a clear look at our data. then we can already estimate a regression line.

As we've said earlier the only variable which we've to find are **b** *(intersection with the y axes)* and **m** *(the slope)*. 

In [86]:
# show data
fig = go.Figure()

fig.add_trace(go.Scatter(x=feature_matrix['petal width (cm)'], y=feature_matrix['petal length (cm)'],
                    mode='markers',
                    name='markers'))

fig.update_xaxes(range=[-1,3], dtick=1)
fig.update_yaxes(range=[-1,10], dtick=1)
fig.show()

**m**: Estimating the slope is very easy, how much do we go up (over the y-axes), if we move 1 step to the right on the x-axis.  
For example, if we take a point in the left corner (0.1, 1.1) and we move 1 step to the right, (1.1, ? ) then we end up 
in points (1.1, 3), (1.1, 3.9) and (1.1, 3.9).  And this is something which we can do multiple times ... to generalizing our estimation
lets say it we take (1, 3.7) then we find points (2, [4.9, 5, 5.1, 5.2, 6.4, 6.7]).
Now, to estimate our slope, we just take the average y delta  
((3 - 1.1) + (3.8 - 1.1) + (3.9 - 1.1) + (4.9 - 3.7) + ... + (6.7 - 3.7)) / 9 = 2.056

Eventhough, it wasn't really necessery to calculate this, 

**b**
Now, knowong that we go 2 steps up, when we move 1 step to the right, where would our intersection on the y axes be? 
I would estimate this around 0.85

## plot our estimation

In [85]:
# Define m & B
m = 2.056
b = 0.85

# Create our line
values = {'x':[], 'y':[]}
for x in np.arange(-1, 3, 0.1):
    
    # our formula
    y = m*x + b
    
    #store the data
    values['x'].append(x)
    values['y'].append(y)


# plot the data
fig = go.Figure()

fig.add_trace(go.Scatter(x=feature_matrix['petal width (cm)'], y=feature_matrix['petal length (cm)'],
                    mode='markers',
                    name='markers'))

fig.add_trace(go.Scatter(**values,
                    mode='lines',
                    name='lines'))

fig.show()

## Result ...
Our regresion line starts very well, but seems to under predict when x > 1.  
The reason for this is, that we only took an sampe of dots 

Mean Square Error
with mean $$\frac{1}{N}\sum_{i=1}^{N}(y_{i} - \bar{y})^{2}$$
or
$$\frac{1}{N}\sum_{i=1}^{N}(y_{i} - (m*x_{i}+b))^{2}$$
$\bar{y}$ is the predicted value while $y_{i}$ is the actual vallue 

In [91]:
# sum of square erros
sse = 0

for x, y_real in zip(feature_matrix['petal width (cm)'], feature_matrix['petal length (cm)']):
    
    # predict y
    y_pred = m*x + b
    sse += (y_real - y_pred)**2
    
mse = sse/len(feature_matrix)

print(f'MSE: {mse}')

MSE: 0.4386079125333333


# Linear Regression - gradient descent with Mean Square Error (MSE)
we're going to estimate a *m* and a *b*, evaluate our *model* via the MSE and then adjust our *m* and *b* a little bit un such a way that in the next iteration, our error is sligtly less


Error
$$E = \frac{1}{N}\sum_{i=1}^{N}(y_{i} - (m*x_{i}+b))^{2}$$

Gradien descent:
with gradient descent, we take the derivative with respect to 


derivative with respect to *m*

$$dm = \frac{1}{N} \sum_{i=1}^{N}(2 (y_{i} - (m*x_{i}+b)) * (-x_{i}) $$
$$dm = \frac{-2}{N} \sum_{i=1}^{N}(y_{i} - (m*x_{i}+b)) * x_{i} $$
$$dm = \frac{-2}{N} \sum_{i=1}^{N}(y_{i} - \bar{y}) * x_{i} $$


do the same for b
$$dm = \frac{1}{N} \sum_{i=1}^{N}(2 (y_{i} - (m*x_{i}+b)) * (-1) $$
$$dm = \frac{-2}{N} \sum_{i=1}^{N}(y_{i} - (m*x_{i}+b)) $$
$$dm = \frac{-2}{N} \sum_{i=1}^{N}(y_{i} - \bar{y}) $$

In [158]:
# initialize
m = 0
b = 0
L = 0.0001

# Constant value
N = len(feature_matrix)

# values_to_plot
to_plot = []
data2plot = Data2Plot()
data2plot.prepare_dynamic_data(name='regression line')
error_x = []
error_y = []
data2plot.prepare_dynamic_data(name='error', panel=2)

for epochs in range(10000):
    X = feature_matrix['petal width (cm)'].values
    Y = feature_matrix['petal length (cm)'].values
    
    # predict the petal length
    Y_pred = m * X + b
    
    # calculate the MSE
    MSE = (1/n) * sum(Y - Y_pred) 
    
    # derivative with respet to m
    m_der = (-2/n) * sum((Y - Y_pred) * X)
    
    # derivative with respet to b
    b_der = (-2/n) * sum(Y - Y_pred)
    
    # update m and b
    m -=  L * m_der
    b -=  L * b_der
    
    # toplot
    if epochs % 100 == 0:
        to_plot.append((X, Y, Y_pred, MSE, m, m_der, b, b_der))
        data2plot.feed_dynamic_data(name='regression line', x= X, y= Y_pred)
        error_x.append(len(error_x)+1)
        error_y.append(MSE)
        data2plot.feed_dynamic_data(name='error', x= error_x.copy(), y= error_y.copy())
    
    print(f'MSE: {MSE}\tm: {m}\tb: {b}\r',end='')

In [161]:
from utils.utility_plots import create_dynamic_h_plot, Data2Plot


# get the data
#X, Y, Y_pred, MSE, m, m_der, b, b_der = zip(* to_plot)

# add static data
data2plot.add_static_data(name= 'petal data', 
                          x= feature_matrix['petal width (cm)'], 
                          y= feature_matrix['petal length (cm)'], mode="markers")


create_dynamic_h_plot(data2plot, title="test",  x_range_2=[0,100], y_range_2=[-0.5, 4.5])

# R² 

In [162]:
https://machinelearningmastery.com/solve-linear-regression-using-linear-algebra/

SyntaxError: invalid syntax (<ipython-input-162-3c96704ff5be>, line 1)

In [107]:
from utils.utility_plots import create_dynamic_h_plot, Data2Plot

data2plot = Data2Plot()

# add static data
data2plot.add_static_data(name= 'housing data', x= feature_matrix.RM, y= target.y, mode="markers", rgb_colour=(0,0,0,0.5))
data2plot.add_static_data(name= 'housing data_2', x= feature_matrix.RM-1, y= target.y, mode="markers", panel=2)

# create dynamic figure
data2plot.prepare_dynamic_data(name='regression line')
data2plot.prepare_dynamic_data(name='regression line 2', panel=2)
data2plot.prepare_dynamic_data(name='regression line 3', panel=3)
for v in [[0,50],[5,45],[10,40],[20,30],[30,20],[40,10],[45,5],[50,0]]:
    data2plot.feed_dynamic_data(name='regression line', x=[3,9], y=v)
    data2plot.feed_dynamic_data(name='regression line 2', x=[3,9], y=(v[1],v[0]))
    data2plot.feed_dynamic_data(name='regression line 3', x=[3,9], y=(v[1],v[0]))
    
    
create_dynamic_h_plot(data2plot, title="test", x_axis_2='xx', y_axis_1='yy', x_range_1=[4,7])


AttributeError: 'DataFrame' object has no attribute 'RM'